In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime, timedelta 
from collections import deque 

In [2]:
pos_db = pd.read_csv('POS_DB.csv')

xls = pd.ExcelFile('Basic_Information_Data.xlsx')
print(xls.sheet_names)

store = pd.read_excel('Basic_Information_Data.xlsx',0)
meal = pd.read_excel('Basic_Information_Data.xlsx',1)
bom = pd.read_excel('Basic_Information_Data.xlsx',2)

material = pd.read_csv('Material_DB.csv')

['Store', 'Meal_Cost', 'BOM']


In [3]:
all = pos_db.merge(store, how = 'left', left_on = 'Restaurant', right_on = 'StoreID')\
    .merge(meal, how = 'left', left_on = 'Meal', right_on='MealID')

all['price'] = all['Sales']/all['Units']
all['Date'] = pd.to_datetime(all['Date'])
all['yymm'] = all['Date'].dt.strftime('%Y-%m')
all['year'] = all['Date'].dt.strftime('%Y')
all['store'] = all['Restaurant'].apply('{0:0>3}'.format) + '-' + all['StoreName']
all.rename(columns = {'MealName':'meal_name'},inplace = True)

In [4]:
df = all[['store','yymm','year','meal_name','price']]
df['average_price'] = round(df.groupby(['store','meal_name'])['price'].transform('mean'),1)
df['month_average_price']= round(all.groupby(['store','yymm','meal_name'])['price'].transform('mean'),1)
df['price_change'] = (df['month_average_price']-df['average_price'])/df['average_price']
#df['price_change'] = df['price_change'].map(lambda x : '{:,.2%}'.format(x))

df = df[df['year'] == '2000']
df.head(10)

C:\Users\erjac\AppData\Local\Temp\ipykernel_24704\2123318507.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['average_price'] = round(df.groupby(['store','meal_name'])['price'].transform('mean'),1)
C:\Users\erjac\AppData\Local\Temp\ipykernel_24704\2123318507.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['month_average_price']= round(all.groupby(['store','yymm','meal_name'])['price'].transform('mean'),1)
C:\Users\erjac\AppData\Local\Temp\ipykernel_24704\2123318507.py:4: SettingWithCopyWarning

store     yymm  year meal_name  price  average_price  \
3712695  001-蒼穹帝國  2000-01  2000     鴨肉香草烤  200.0          194.4   
3712696  001-蒼穹帝國  2000-01  2000      鴨肉炒飯   96.0           93.1   
3712697  001-蒼穹帝國  2000-01  2000       鴨肉湯   40.0           38.7   
3712698  001-蒼穹帝國  2000-01  2000       鴨肉湯   40.0           38.7   
3712699  001-蒼穹帝國  2000-01  2000       鴨肉湯   40.0           38.7   
3712700  001-蒼穹帝國  2000-01  2000   鴨肉麻辣燴豆腐  160.0          157.4   
3712701  001-蒼穹帝國  2000-01  2000     鴨肉麵線湯   96.0           93.3   
3712702  001-蒼穹帝國  2000-01  2000     鴨肉香草烤  200.0          194.4   
3712703  001-蒼穹帝國  2000-01  2000      鴨肉炒飯   96.0           93.1   
3712704  001-蒼穹帝國  2000-01  2000     鴨肉麵線湯   86.5           93.3   

         month_average_price  price_change  
3712695                195.3      0.004630  
3712696                 93.2      0.001074  
3712697                 38.9      0.005168  
3712698                 38.9      0.005168  
3712699                 38.9      0.005168  
3712700                157.8      0.002541  
3712701                 93.2     -0.001072  
3712702                195.3      0.004630  
3712703                 93.2      0.001074  
3712704                 93.2     -0.001072

In [5]:
meal_list = list(df['meal_name'].unique())

price_change_pivot = {}

for meal in meal_list:
    meal_df = df[df.meal_name == meal]
    pivot_table  = meal_df.pivot_table(values = "month_average_price",index = ['store','average_price'],columns = 'yymm')
    price_change_pivot[meal] = pivot_table
    

price_change_pivot[meal_list[0]]

yymm                    2000-01  2000-02  2000-03  2000-04  2000-05  2000-06  \
store    average_price                                                         
001-蒼穹帝國 194.4            195.3    195.6    195.0    194.4    194.3    194.9   
002-龍鱗大陸 242.9            244.2    243.8    244.0    243.1    243.0    243.8   
003-星光之海 242.8            245.0    245.5    245.0    244.8    245.2    245.7   
004-霜雪之峰 340.3            341.6    342.4    341.1    340.4    340.9    341.5   
005-雲煙古都 242.9            243.9    244.1    242.9    242.3    242.6    243.1   
006-銀翼城市 389.2            390.6    390.6    388.9    387.3    389.4    391.3   
007-黃金沙漠 312.7            315.0    314.2    313.5    312.3    313.5    314.1   
008-星火之谷 486.5            488.2    489.3    486.8    485.1    487.5    488.4   
009-虹彩島  146.1            146.7    146.6    146.0    146.2    146.3    146.6   
010-魔法禁地 121.2            121.8    121.6    121.6    121.0    121.1    121.6   

yymm                    2000-07  2000-08  2000-09  2000-10  2000-11  2000-12  
store    average_price                                                        
001-蒼穹帝國 194.4            195.2    195.2    194.6    194.0    194.4    195.0  
002-龍鱗大陸 242.9            243.7    243.8    243.0    242.7    243.3    243.4  
003-星光之海 242.8            245.8    245.4    245.8    245.6    245.6    245.9  
004-霜雪之峰 340.3            341.4    340.9    340.0    340.6    340.4    341.6  
005-雲煙古都 242.9            244.1    244.0    243.2    243.7    242.6    243.7  
006-銀翼城市 389.2            390.0    389.3    390.3    389.1    390.1    390.3  
007-黃金沙漠 312.7            315.1    314.1    312.8    312.5    312.8    314.1  
008-星火之谷 486.5            488.9    488.4    487.4    486.6    487.3    488.3  
009-虹彩島  146.1            146.7    146.6    146.6    146.2    145.9    146.3  
010-魔法禁地 121.2            121.8    121.6    121.0    121.0    121.2    121.5

In [6]:
cv = lambda x: round(np.std(x, ddof=1) / np.mean(x) * 100,2)
df2 = df.groupby(['store','meal_name'])['price'].apply(cv)
df2 = pd.DataFrame(df2)
cv_pivot = df2.pivot_table(index = 'meal_name',columns = 'store')
cv_pivot

price                                                        \
store     001-蒼穹帝國 002-龍鱗大陸 003-星光之海 004-霜雪之峰 005-雲煙古都 006-銀翼城市 007-黃金沙漠   
meal_name                                                                  
鴨肉湯           4.75     4.54     4.21     4.64     4.40     4.99     3.76   
鴨肉炒飯          4.63     4.50     4.68     4.74     4.71     4.40     4.80   
鴨肉香草烤         4.50     4.51     3.94     4.48     4.53     4.48     4.94   
鴨肉麵線湯         4.54     4.49     4.69     4.59     4.58     4.24     4.66   
鴨肉麻辣燴豆腐       3.94     4.52     4.68     4.02     4.16     3.87     3.45   

                                     
store     008-星火之谷 009-虹彩島 010-魔法禁地  
meal_name                            
鴨肉湯           4.40    4.31     4.79  
鴨肉炒飯          4.89    4.74     4.55  
鴨肉香草烤         4.42    4.38     4.66  
鴨肉麵線湯         4.75    4.61     4.43  
鴨肉麻辣燴豆腐       3.63    4.52     4.12

In [7]:
material_expire = {
    'material':['米', '鴨肉片', '麵線', '全鴨', '香草', '豆腐', '特殊辣香料'],
    'days':[800,90,800,90,2000,90,2000]
}

material_expire = pd.DataFrame(material_expire)
material_expire

material  days
0        米   800
1      鴨肉片    90
2       麵線   800
3       全鴨    90
4       香草  2000
5       豆腐    90
6    特殊辣香料  2000

In [8]:
material_out = all.merge(bom,how = 'left',left_on = 'MealID',right_on = 'MealID')
material_out['Sales_Number'] = material_out ['Units_x'] * material_out['Units_y']
material_out= pd.DataFrame(material_out.groupby(['Restaurant','Material','Date'])['Sales_Number'].sum().reset_index())
material_out

Restaurant Material       Date  Sales_Number
0                1       全鴨 1995-01-01           110
1                1       全鴨 1995-01-02           100
2                1       全鴨 1995-01-03            76
3                1       全鴨 1995-01-04           137
4                1       全鴨 1995-01-05           137
...            ...      ...        ...           ...
131515          10       麵線 2000-12-27           249
131516          10       麵線 2000-12-28           239
131517          10       麵線 2000-12-29           213
131518          10       麵線 2000-12-30           244
131519          10       麵線 2000-12-31           218

[131520 rows x 4 columns]

In [9]:
material_in = material.merge(material_expire,how = 'left', left_on= 'Material', right_on= 'material')
material_in['Delivery_Date'] = pd.to_datetime(material_in['Delivery_Date'])
material_in['expire_date'] =  material_in['Delivery_Date'] + pd.to_timedelta(material_in['days'],unit='D')
material_in = material_in[['Restaurant','Material_Order_ID','Material','Delivery_Date','expire_date','Order_Number']]
material_in.sort_values(['Restaurant','Material','Delivery_Date'],inplace=True)
material_in.reset_index(inplace=True,drop=True)

In [10]:
material_in.head()

Restaurant Material_Order_ID Material Delivery_Date expire_date  \
0           1      R1M003000001       全鴨    1995-01-01  1995-04-01   
1           1      R1M003000002       全鴨    1995-01-12  1995-04-12   
2           1      R1M003000003       全鴨    1995-01-28  1995-04-28   
3           1      R1M003000004       全鴨    1995-02-13  1995-05-14   
4           1      R1M003000005       全鴨    1995-02-26  1995-05-27   

   Order_Number  
0        1500.0  
1        1500.0  
2        1500.0  
3        1500.0  
4        1500.0

In [18]:
# 根據餐廳、物料和日期排序
material_in = material_in.sort_values(['Restaurant', 'Material', 'Delivery_Date'])
material_out = material_out.sort_values(['Restaurant', 'Material', 'Date'])

# 初始化庫存和報廢量
inventory = {(row['Restaurant'], row['Material']): [] for _, row in material_in.iterrows()}
waste_by_restaurant_material = {(row['Restaurant'], row['Material']): 0 for _, row in material_in.iterrows()}

# 處理進貨
for _, row in material_in.iterrows():
    key = (row['Restaurant'], row['Material'])
    inventory[key].append({'expire_date': row['expire_date'], 'quantity': row['Order_Number']})

# 處理出貨和報廢
for _, row in material_out.iterrows():
    key = (row['Restaurant'], row['Material'])
    sale_date = row['Date']
    sale_quantity = row['Sales_Number']
    
    # 處理每筆庫存
    for stock in inventory[key]:
        # 檢查並處理報廢
        if stock['expire_date'] < sale_date: # 檢查該批庫存是否過期
            print(f"餐廳 {key[0]}, 食材 {key[1]}: 一批庫存已過期，數量 {stock['quantity']}, 日期 {stock['expire_date']}")
            waste_by_restaurant_material[key] += stock['quantity'] # 若該庫存已過期，計入報廢量dict
            stock['quantity'] = 0 # 庫存已記入報廢就登記為0

        # 處理出貨
        elif stock['quantity'] > 0: # 若庫存未過期且數量大於0
            if stock['quantity'] >= sale_quantity:  # 若庫存數量大於銷售所使用的數量，進行庫存消耗計算
                print(f"餐廳 {key[0]}, 食材 {key[1]}: 使用了 {sale_quantity} 的庫存，剩餘庫存量：{stock['quantity'] - sale_quantity}")
                stock['quantity'] -= sale_quantity
                sale_quantity = 0 
                break
            else: # 若庫存數量小於銷售所使用的數量，計算使用剩餘庫存後的數量，並以下一批庫存進行消耗使用
                print(f"餐廳 {key[0]}, 食材 {key[1]}: 完全使用了一批庫存，數量：{stock['quantity']}, 還需要：{sale_quantity - stock['quantity']}")
                sale_quantity -= stock['quantity']
                stock['quantity'] = 0

    # 移除已經用完的庫存
    inventory[key] = [stock for stock in inventory[key] if stock['quantity'] > 0]



餐廳 1, 食材 全鴨: 使用了 110 的庫存，剩餘庫存量：1390.0
餐廳 1, 食材 全鴨: 使用了 100 的庫存，剩餘庫存量：1290.0
餐廳 1, 食材 全鴨: 使用了 76 的庫存，剩餘庫存量：1214.0
餐廳 1, 食材 全鴨: 使用了 137 的庫存，剩餘庫存量：1077.0
餐廳 1, 食材 全鴨: 使用了 137 的庫存，剩餘庫存量：940.0
餐廳 1, 食材 全鴨: 使用了 124 的庫存，剩餘庫存量：816.0
餐廳 1, 食材 全鴨: 使用了 148 的庫存，剩餘庫存量：668.0
餐廳 1, 食材 全鴨: 使用了 81 的庫存，剩餘庫存量：587.0
餐廳 1, 食材 全鴨: 使用了 80 的庫存，剩餘庫存量：507.0
餐廳 1, 食材 全鴨: 使用了 96 的庫存，剩餘庫存量：411.0
餐廳 1, 食材 全鴨: 使用了 107 的庫存，剩餘庫存量：304.0
餐廳 1, 食材 全鴨: 使用了 146 的庫存，剩餘庫存量：158.0
餐廳 1, 食材 全鴨: 使用了 69 的庫存，剩餘庫存量：89.0
餐廳 1, 食材 全鴨: 使用了 77 的庫存，剩餘庫存量：12.0
餐廳 1, 食材 全鴨: 完全使用了一批庫存，數量：12.0, 還需要：97.0
餐廳 1, 食材 全鴨: 使用了 97.0 的庫存，剩餘庫存量：1403.0
餐廳 1, 食材 全鴨: 使用了 123 的庫存，剩餘庫存量：1280.0
餐廳 1, 食材 全鴨: 使用了 90 的庫存，剩餘庫存量：1190.0
餐廳 1, 食材 全鴨: 使用了 98 的庫存，剩餘庫存量：1092.0
餐廳 1, 食材 全鴨: 使用了 109 的庫存，剩餘庫存量：983.0
餐廳 1, 食材 全鴨: 使用了 47 的庫存，剩餘庫存量：936.0
餐廳 1, 食材 全鴨: 使用了 95 的庫存，剩餘庫存量：841.0
餐廳 1, 食材 全鴨: 使用了 64 的庫存，剩餘庫存量：777.0
餐廳 1, 食材 全鴨: 使用了 126 的庫存，剩餘庫存量：651.0
餐廳 1, 食材 全鴨: 使用了 102 的庫存，剩餘庫存量：549.0
餐廳 1, 食材 全鴨: 使用了 56 的庫存，剩餘庫存量：493.0
餐廳 1, 食材 全鴨: 使用了 83 的庫存，剩餘庫存量：410.0
餐廳 

In [19]:
# 顯示每家餐廳每種食材的總報廢量
for (restaurants, materials), total_waste in waste_by_restaurant_material.items():
    print(f'餐廳 {restaurants}, 食材 {materials}: 總報廢量 = {total_waste}')

餐廳 1, 食材 全鴨: 總報廢量 = 0
餐廳 1, 食材 特殊辣香料: 總報廢量 = 0
餐廳 1, 食材 米: 總報廢量 = 0
餐廳 1, 食材 豆腐: 總報廢量 = 0
餐廳 1, 食材 香草: 總報廢量 = 0
餐廳 1, 食材 鴨肉片: 總報廢量 = 0
餐廳 1, 食材 麵線: 總報廢量 = 0
餐廳 2, 食材 全鴨: 總報廢量 = 66820.0
餐廳 2, 食材 特殊辣香料: 總報廢量 = 0
餐廳 2, 食材 米: 總報廢量 = 0
餐廳 2, 食材 豆腐: 總報廢量 = 183462.0
餐廳 2, 食材 香草: 總報廢量 = 0
餐廳 2, 食材 鴨肉片: 總報廢量 = 380322.0
餐廳 2, 食材 麵線: 總報廢量 = 0
餐廳 3, 食材 全鴨: 總報廢量 = 0
餐廳 3, 食材 特殊辣香料: 總報廢量 = 0
餐廳 3, 食材 米: 總報廢量 = 0
餐廳 3, 食材 豆腐: 總報廢量 = 0
餐廳 3, 食材 香草: 總報廢量 = 0
餐廳 3, 食材 鴨肉片: 總報廢量 = 0
餐廳 3, 食材 麵線: 總報廢量 = 0
餐廳 4, 食材 全鴨: 總報廢量 = 53301.0
餐廳 4, 食材 特殊辣香料: 總報廢量 = 0
餐廳 4, 食材 米: 總報廢量 = 0
餐廳 4, 食材 豆腐: 總報廢量 = 21457.0
餐廳 4, 食材 香草: 總報廢量 = 0
餐廳 4, 食材 鴨肉片: 總報廢量 = 341175.0
餐廳 4, 食材 麵線: 總報廢量 = 0
餐廳 5, 食材 全鴨: 總報廢量 = 39815.0
餐廳 5, 食材 特殊辣香料: 總報廢量 = 0
餐廳 5, 食材 米: 總報廢量 = 0
餐廳 5, 食材 豆腐: 總報廢量 = 28874.0
餐廳 5, 食材 香草: 總報廢量 = 0
餐廳 5, 食材 鴨肉片: 總報廢量 = 214107.0
餐廳 5, 食材 麵線: 總報廢量 = 0
餐廳 6, 食材 全鴨: 總報廢量 = 0
餐廳 6, 食材 特殊辣香料: 總報廢量 = 0
餐廳 6, 食材 米: 總報廢量 = 0
餐廳 6, 食材 豆腐: 總報廢量 = 0
餐廳 6, 食材 香草: 總報廢量 = 0
餐廳 6, 食材 鴨肉片: 總報廢量 = 0
餐廳 6, 食材 麵線: 總報廢量 = 0


In [20]:
waste_df = pd.DataFrame(list(waste_by_restaurant_material.items()), columns=['Restaurant_Material', 'Total_Waste'])
waste_df['Restaurant'] = waste_df['Restaurant_Material'].apply(lambda x: x[0])
waste_df['Material'] = waste_df['Restaurant_Material'].apply(lambda x: x[1])
waste_df.drop('Restaurant_Material', axis=1, inplace=True)
waste_df = waste_df.merge(all[['Restaurant','store']].drop_duplicates('store').sort_values('Restaurant'),how = 'left',left_on = 'Restaurant',right_on='Restaurant')
waste_df.drop(columns='Restaurant',inplace= True)

In [21]:
waste_pivot =waste_df.pivot_table(index='Material',columns='store')
waste_pivot

Total_Waste                                                           \
store       001-蒼穹帝國  002-龍鱗大陸 003-星光之海  004-霜雪之峰  005-雲煙古都 006-銀翼城市 007-黃金沙漠   
Material                                                                        
全鴨               0.0   66820.0      0.0   53301.0   39815.0      0.0      0.0   
特殊辣香料            0.0       0.0      0.0       0.0       0.0      0.0      0.0   
米                0.0       0.0      0.0       0.0       0.0      0.0      0.0   
豆腐               0.0  183462.0      0.0   21457.0   28874.0      0.0      0.0   
香草               0.0       0.0      0.0       0.0       0.0      0.0      0.0   
鴨肉片              0.0  380322.0      0.0  341175.0  214107.0      0.0      0.0   
麵線               0.0       0.0      0.0       0.0       0.0      0.0      0.0   

                                    
store    008-星火之谷 009-虹彩島 010-魔法禁地  
Material                            
全鴨            0.0     0.0      0.0  
特殊辣香料         0.0     0.0      0.0  
米             0.0     0.0      0.0  
豆腐            0.0     0.0      0.0  
香草            0.0     0.0      0.0  
鴨肉片           0.0     0.0      0.0  
麵線            0.0     0.0      0.0